In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

from kaggle_secrets import UserSecretsClient
user_secrets = UserSecretsClient()
secret_value = user_secrets.get_secret("personal_token")

!pip install git+https://{secret_value}@github.com/DimbyTa/clrs_32.git

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import clrs
from clrs._src.algorithms import graphs
from clrs._src.processors import get_processor_factory
import jax
import tensorflow as tf
import functools
import shutil
from typing import Any, Dict, List
from absl import logging
import requests
# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

  Cloning https://****@github.com/DimbyTa/clrs_32.git to /tmp/pip-req-build-upn7cjp7
  Running command git clone --filter=blob:none --quiet 'https://****@github.com/DimbyTa/clrs_32.git' /tmp/pip-req-build-upn7cjp7
  Resolved https://****@github.com/DimbyTa/clrs_32.git to commit f97172d2825b83b7cf44255224c27d3b15ffb644
  Preparing metadata (setup.py) ... - done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 352.1/352.1 kB 7.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.3/4.3 MB 64.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 55.5 MB/s eta 0:00:00
  Created wheel for dm-clrs: filename=dm_clrs-1.0.0-py3-none-any.whl size=113787 sha256=4ce545e3fa682787a89bd2b62cc9b6a3a94c1bb0e17fa36c269e60fe28103be2
  Stored in directory: /tmp/pip-ephem-wheel-cache-vv1j500m/wheels/b1/d0/3f/4b2e080f87c791ed05809ef3fea8b31f95898fdcfbe416f672
Successfully built dm-clrs
  Attempting uninstall: protobuf
    Found existing installation: protobuf 3.20.3
    Unin

In [2]:
#python3 -m clrs.examples.run

# Création du modèle

In [3]:
class functionalGNN:
    """
    Inspired by run.py in examples directory of clrs
    """
    def __init__(self, processor: str, algorithm: str, name: str):
        """
        initialize a functional GNN with
        processor: one of the allowed GNN architecture to chose from
        algorithm: the algorithm we want to imitate
        name: the name of this GNN model
        """
        # Initialize model
        self.model = None
        
        #Which algorithms to run.
        self.algorithms = [algorithm]
        
        #Which training sizes to use. A size of -1 means use the benchmark dataset.
        #self.train_lengths = ['4', '7', '10', '11', '13']
        self.train_lengths = ['4']
        
        #Length of needle for training and validation (not testing) in string matching algorithms.
        #A negative value randomizes the length for each sample between 1 and the opposite of the value.
        #A value of 0 means use always 1/4 of the length of the haystack (the default sampler behavior).
        self.length_needle = -8
        
        #Random seed to set for Random Number Generator
        self.seed = 42

        #Randomize the pos input common to all algos.
        self.random_pos = True
        
        #Whether to enforce permutation-type node pointers.
        self.enforce_permutations = True
        
        #Whether to change pred_h hints into pred inputs.
        self.enforce_pred_as_input = True
        
        #Batch size used for training.
        self.batch_size = 32
        
        #Whether to use chunking for training.
        self.chunked_training = False
        
        #Time chunk length used for training (if chunked_training` is True.
        self.chunk_length = 16
        
        #Number of training iterations.
        self.train_steps = 10000
        
        #Evaluation frequency (in steps).
        self.eval_every = 50
        
        #Evaluation frequency (in steps). OOD
        self.test_every = 500

        #Number of hidden units of the model.
        self.hidden_size = 128
        
        #Number of heads for GAT processors
        self.nb_heads = 1
        
        #Number of message passing steps to run per hint.
        self.nb_msg_passing_steps = 1
        
        #Learning rate to use.
        self.learning_rate = 0.001
        
        #Gradient clipping by norm. 0.0 disables grad clipping
        self.grad_clip_max_norm = 1.0
        
        #Dropout rate to use.
        self.dropout_prob = 0.0
        
        #Probability that ground-truth teacher hints are encoded during 
        #training instead of predicted hints. Only pertinent in encoded_decoded modes.
        self.hint_teacher_forcing = 0.0
        
        
        # One of ['encoded_decoded', 'decoded_only', 'none'],
        # How should hints be used? Note, each mode defines a 
        # separate task, with various difficulties. `encoded_decoded` 
        # requires the model to explicitly materialise hint sequences 
        # and therefore is hardest, but also most aligned to the 
        # underlying algorithmic rule. Hence, `encoded_decoded` 
        # should be treated as the default mode for our benchmark. 
        # In `decoded_only`, hints are only used for defining 
        # reconstruction losses. Often, this will perform well, but 
        # note that we currently do not make any efforts to 
        # counterbalance the various hint losses. Hence, for certain 
        # tasks, the best performance will now be achievable with no 
        # hint usage at all (`none`).
        self.hint_mode= 'encoded_decoded'
        
        # One of ['soft', 'hard', 'hard_on_eval'],
        # How to process predicted hints when fed back as inputs.
        # In soft mode, we use softmaxes for categoricals, pointers 
        # and mask_one, and sigmoids for masks. 
        # In hard mode, we use argmax instead of softmax, and hard 
        # thresholding of masks. 
        # In hard_on_eval mode, soft mode is 
        # used for training and hard mode is used for evaluation.
        self.hint_repred_mode = 'soft'
        
        #Whether to use layer normalisation in the processor.
        self.use_ln = True
        
        # Whether to insert an LSTM after message passing.
        self.use_lstm = False
        
        # How many triplet features to compute?
        self.nb_triplet_fts = 8

        # One of ['default', 'xavier_on_scalars']
        # Initialiser to use for the encoders.
        self.encoder_init = 'xavier_on_scalars'
        
        # One of ['deepsets', 'mpnn', 'pgn', 'pgn_mask',
        # 'triplet_mpnn', 'triplet_pgn', 'triplet_pgn_mask',
        # 'gat', 'gatv2', 'gat_full', 'gatv2_full',
        # 'gpgn', 'gpgn_mask', 'gmpnn',
        # 'triplet_gpgn', 'triplet_gpgn_mask', 'triplet_gmpnn'],
        # Processor type to use as the network P.
        self.processor_type = processor

        # Path in which checkpoints are saved.')
        self.checkpoint_path = '/tmp/CLRS30' + '/' + name
        # Path in which dataset is stored.')
        self.dataset_path = '/tmp/CLRS30/dataset'
        
        #val_score_record
        self.record_val = []
        self.name = name
        self.record_test = None
        
        # Whether to freeze the processor of the model.')
        self.freeze_processor = False
        self.PRED_AS_INPUT_ALGOS = [
            'binary_search',
            'minimum',
            'find_maximum_subarray',
            'find_maximum_subarray_kadane',
            'matrix_chain_order',
            'lcs_length',
            'optimal_bst',
            'activity_selector',
            'task_scheduling',
            'naive_string_matcher',
            'kmp_matcher',
            'jarvis_march']
    
    def unpack(self,v):
        try:
            return v.item()  # DeviceArray
        except (AttributeError, ValueError):
            return v


    def _iterate_sampler(self,sampler, batch_size):
        while True:
            yield sampler.next(batch_size)


    def _maybe_download_dataset(self,dataset_path):
        """Download CLRS30 dataset if needed."""
        dataset_folder = os.path.join(dataset_path, clrs.get_clrs_folder())
        if os.path.isdir(dataset_folder):
            #logging.info('Dataset found at %s. Skipping download.', dataset_folder)
            print('Dataset found at %s. Skipping download.'% (dataset_folder,))
            return dataset_folder
        #logging.info('Dataset not found in %s. Downloading...', dataset_folder)
        print('Dataset not found in %s. Downloading...'% dataset_folder)
        clrs_url = clrs.get_dataset_gcp_url()
        request = requests.get(clrs_url, allow_redirects=True)
        clrs_file = os.path.join(dataset_path, os.path.basename(clrs_url))
        os.makedirs(dataset_folder)
        open(clrs_file, 'wb').write(request.content)
        shutil.unpack_archive(clrs_file, extract_dir=dataset_folder)
        os.remove(clrs_file)
        return dataset_folder


    def make_sampler(self,length: int,
                     rng: Any,
                     algorithm: str,
                     split: str,
                     batch_size: int,
                     multiplier: int,
                     randomize_pos: bool,
                     enforce_pred_as_input: bool,
                     enforce_permutations: bool,
                     chunked: bool,
                     chunk_length: int,
                     sampler_kwargs: Dict[str, Any]):
        """Create a sampler with given options.

          Args:
            length: Size of samples (i.e., number of nodes in the graph).
              A length of -1 will mean that the benchmark
              dataset (for the given split) is used. Positive sizes will instantiate
              samplers of the corresponding size.
            rng: Numpy random state.
            algorithm: The name of the algorithm to sample from.
            split: 'train', 'val' or 'test'.
            batch_size: Samples per batch.
            multiplier: Integer multiplier for the number of samples in the dataset,
              only used for positive sizes. Negative multiplier means infinite samples.
            randomize_pos: Whether to randomize the `pos` input.
            enforce_pred_as_input: Whether to convert fixed pred_h hints to inputs.
            enforce_permutations: Whether to enforce permutation pointers.
            chunked: Whether to chunk the dataset.
            chunk_length: Unroll length of chunks, if `chunked` is True.
            sampler_kwargs: Extra args passed to the sampler.
          Returns:
            A sampler (iterator), the number of samples in the iterator (negative
            if infinite samples), and the spec.
        """
        if length < 0:  # load from file
            dataset_folder = self._maybe_download_dataset(self.dataset_path)
            sampler, num_samples, spec = clrs.create_dataset(folder=dataset_folder,
                                                         algorithm=algorithm,
                                                         batch_size=batch_size,
                                                         split=split)
            sampler = sampler.as_numpy_iterator()
        else:
            num_samples = clrs.CLRS30[split]['num_samples'] * multiplier
            #if algorithm=='hlflow_mincut':
                #num_samples = clrs.CLRS30[split]['num_samples'] * multiplier
                #if num_samples > 100 and split=='train':
                    #num_samples = 100
            #else:
                #num_samples = clrs.CLRS30[split]['num_samples'] * multiplier
            print("num_samples ", num_samples)
            sampler, spec = clrs.build_sampler(algorithm,
                #seed=rng.randint(32),
                seed=42,
                num_samples=num_samples,
                length=length,
                **sampler_kwargs,
                )
            print("Iterating sampler")
            sampler = self._iterate_sampler(sampler, batch_size)
        if randomize_pos:
            sampler = clrs.process_random_pos(sampler, rng)
        if enforce_pred_as_input and algorithm in self.PRED_AS_INPUT_ALGOS:
            spec, sampler = clrs.process_pred_as_input(spec, sampler)
        spec, sampler = clrs.process_permutations(spec, sampler, enforce_permutations)
        if chunked:
            sampler = clrs.chunkify(sampler, chunk_length)
        print("returning sampler for ", split)
        return sampler, num_samples, spec
    
    def make_multi_sampler(self,sizes, rng, **kwargs):
        """Create a sampler with cycling sample sizes."""
        ss = []
        tot_samples = 0
        for length in sizes:
            sampler, num_samples, spec = self.make_sampler(length, rng, **kwargs)
            ss.append(sampler)
            tot_samples += num_samples
        def cycle_samplers():
            while True:
                for s in ss:
                    yield next(s)
        return cycle_samplers(), tot_samples, spec


    def _concat(self,dps, axis):
        return jax.tree_util.tree_map(lambda *x: np.concatenate(x, axis), *dps)


    def collect_and_eval(self,sampler, predict_fn, sample_count, rng_key, extras):
        """Collect batches of output and hint preds and evaluate them."""
        processed_samples = 0
        preds = []
        outputs = []
        while processed_samples < sample_count:
            feedback = next(sampler)
            batch_size = feedback.outputs[0].data.shape[0]
            outputs.append(feedback.outputs)
            new_rng_key, rng_key = jax.random.split(rng_key)
            cur_preds, _ = predict_fn(new_rng_key, feedback.features)
            preds.append(cur_preds)
            processed_samples += batch_size
        outputs = self._concat(outputs, axis=0)
        preds = self._concat(preds, axis=0)
        out = clrs.evaluate(outputs, preds)
        if extras:
            out.update(extras)
        return {k: self.unpack(v) for k, v in out.items()}


    def create_samplers(self,rng, train_lengths: List[int]):
        """Create all the samplers."""
        train_samplers = []
        val_samplers = []
        val_sample_counts = []
        test_samplers = []
        test_sample_counts = []
        spec_list = []
        for algo_idx, algorithm in enumerate(self.algorithms):
            # Make full dataset pipeline run on CPU (including prefetching).
            with tf.device('/cpu:0'):
                if algorithm in ['naive_string_matcher', 'kmp_matcher']:
                    # Fixed haystack + needle; variability will be in needle
                    # Still, for chunked training, we maintain as many samplers
                    # as train lengths, since, for each length there is a separate state,
                    # and we must keep the 1:1 relationship between states and samplers.
                    max_length = max(train_lengths)
                    if max_length > 0:  # if < 0, we are using the benchmark data
                        max_length = (max_length * 5) // 4
                    train_lengths = [max_length]
                    if self.chunked_training:
                        train_lengths = train_lengths * len(train_lengths)
                #logging.info('Creating samplers for algo %s', algorithm)
                print('Creating samplers for algo %s'% algorithm)
                p = tuple([0.1 + 0.1 * i for i in range(9)])
                if p and algorithm in ['articulation_points', 'bridges',
                                 'mst_kruskal', 'bipartite_matching','hlflow_mincut']:
                    # Choose a lower connection probability for the above algorithms,
                    # otherwise trajectories are very long
                    p = tuple(np.array(p) / 2)
                length_needle = self.length_needle
                sampler_kwargs = dict(p=p, length_needle=length_needle)
                if length_needle == 0:
                    sampler_kwargs.pop('length_needle')
                common_sampler_args = dict(
                  algorithm=self.algorithms[algo_idx],
                  rng=rng,
                  enforce_pred_as_input=self.enforce_pred_as_input,
                  enforce_permutations=self.enforce_permutations,
                  chunk_length=self.chunk_length,
                  )
                train_args = dict(sizes=train_lengths,
                            split='train',
                            batch_size=self.batch_size,
                            multiplier=1,
                            randomize_pos=self.random_pos,
                            chunked=self.chunked_training,
                            sampler_kwargs=sampler_kwargs,
                            **common_sampler_args)
                train_sampler, _, spec = self.make_multi_sampler(**train_args)
                
                mult = clrs.CLRS_30_ALGS_SETTINGS[algorithm]['num_samples_multiplier']
                val_args = dict(sizes=[np.amax(train_lengths)],
                          split='val',
                          batch_size=32,
                          multiplier=2 * mult,
                          randomize_pos=self.random_pos,
                          chunked=False,
                          sampler_kwargs=sampler_kwargs,
                          **common_sampler_args)
                val_sampler, val_samples, spec = self.make_multi_sampler(**val_args)
                test_args = dict(sizes=[-1],
                           split='test',
                           batch_size=32,
                           multiplier=2 * mult,
                           randomize_pos=False,
                           chunked=False,
                           sampler_kwargs={},
                           **common_sampler_args)
                test_sampler, test_samples, spec = self.make_multi_sampler(**test_args)

        spec_list.append(spec)
        train_samplers.append(train_sampler)
        val_samplers.append(val_sampler)
        val_sample_counts.append(val_samples)
        test_samplers.append(test_sampler)
        test_sample_counts.append(test_samples)
        return (train_samplers,
              val_samplers, val_sample_counts,
              test_samplers, test_sample_counts,
              spec_list)
    def train(self):
        """
        Main training loop
        """
        if self.hint_mode == 'encoded_decoded':
            encode_hints = True
            decode_hints = True
        elif self.hint_mode == 'decoded_only':
            encode_hints = False
            decode_hints = True
        elif self.hint_mode == 'none':
            encode_hints = False
            decode_hints = False
        else:
            raise ValueError('Hint mode not in {encoded_decoded, decoded_only, none}.')
        
        train_lengths = [int(x) for x in self.train_lengths]
        rng = np.random.RandomState(self.seed)
        rng_key = jax.random.PRNGKey(rng.randint(2**32))
        
        # Create samplers
        (train_samplers,
       val_samplers, val_sample_counts,
       test_samplers, test_sample_counts,
       spec_list) = self.create_samplers(rng, train_lengths)
        processor_factory = clrs.get_processor_factory(
          self.processor_type,
          use_ln=self.use_ln,
          nb_triplet_fts=self.nb_triplet_fts,
          nb_heads=self.nb_heads
      )
        model_params = dict(
          processor_factory=processor_factory,
          hidden_dim=self.hidden_size,
          encode_hints=encode_hints,
          decode_hints=decode_hints,
          encoder_init=self.encoder_init,
          use_lstm=self.use_lstm,
          learning_rate=self.learning_rate,
          grad_clip_max_norm=self.grad_clip_max_norm,
          checkpoint_path=self.checkpoint_path,
          freeze_processor=self.freeze_processor,
          dropout_prob=self.dropout_prob,
          hint_teacher_forcing=self.hint_teacher_forcing,
          hint_repred_mode=self.hint_repred_mode,
          nb_msg_passing_steps=self.nb_msg_passing_steps,
          )
        eval_model = clrs.models.BaselineModel(
          spec=spec_list,
          dummy_trajectory=[next(t) for t in val_samplers],
          **model_params
        )
        if self.chunked_training:
            train_model = clrs.models.BaselineModelChunked(
                spec=spec_list,
                dummy_trajectory=[next(t) for t in train_samplers],
                **model_params
            )
        else:
            train_model = eval_model
        # Training loop.
        best_score = -1.0
        current_train_items = [0] * len(self.algorithms)
        step = 0
        next_eval = 0
        # Make sure scores improve on first step, but not overcome best score
        # until all algos have had at least one evaluation.
        val_scores = [-99999.9] * len(self.algorithms)
        length_idx = 0
        while step < self.train_steps:
            feedback_list = [next(t) for t in train_samplers]
            # Initialize model.
            if step == 0:
                all_features = [f.features for f in feedback_list]
                if self.chunked_training:
                    # We need to initialize the model with samples of all lengths for
                    # all algorithms. Also, we need to make sure that the order of these
                    # sample sizes is the same as the order of the actual training sizes.
                    all_length_features = [all_features] + [
                        [next(t).features for t in train_samplers]
                         for _ in range(len(train_lengths))]
                    train_model.init(all_length_features[:-1], self.seed + 1)
                else:
                    train_model.init(all_features, self.seed + 1)
            # Training step.
            for algo_idx in range(len(train_samplers)):
                feedback = feedback_list[algo_idx]
                rng_key, new_rng_key = jax.random.split(rng_key)
                if self.chunked_training:
                    # In chunked training, we must indicate which training length we are
                    # using, so the model uses the correct state.
                    length_and_algo_idx = (length_idx, algo_idx)
                else:
                    # In non-chunked training, all training lengths can be treated equally,
                    # since there is no state to maintain between batches.
                    length_and_algo_idx = algo_idx
                    cur_loss = train_model.feedback(rng_key, feedback, length_and_algo_idx)
                    rng_key = new_rng_key
                if self.chunked_training:
                    examples_in_chunk = np.sum(feedback.features.is_last).item()
                else:
                    examples_in_chunk = len(feedback.features.lengths)
                    current_train_items[algo_idx] += examples_in_chunk
                    #logging.info('Algo %s step %i current loss %f, current_train_items %i.',
                       #self.algorithms[algo_idx], step,
                       #cur_loss, current_train_items[algo_idx])
                    print('Algo %s step %i current loss %f, current_train_items %i.'%
                       (self.algorithms[algo_idx], step,
                       cur_loss, current_train_items[algo_idx]))
            # Periodically evaluate model
            if step >= next_eval:
                eval_model.params = train_model.params
                for algo_idx in range(len(train_samplers)):
                    common_extras = {'examples_seen': current_train_items[algo_idx],
                             'step': step,
                             'algorithm': self.algorithms[algo_idx]}
                    # Validation info.
                    new_rng_key, rng_key = jax.random.split(rng_key)
                    val_stats = self.collect_and_eval(
                                    val_samplers[algo_idx],
                                    functools.partial(eval_model.predict, algorithm_index=algo_idx),
                                    val_sample_counts[algo_idx],
                                    new_rng_key,
                                    extras=common_extras)
                    #logging.info('(val) algo %s step %d: %s',
                         #self.algorithms[algo_idx], step, val_stats)
                    print('(val) algo %s step %d: %s'%
                         (self.algorithms[algo_idx], step, val_stats))
                    self.record_val.append({'step': step, 'score': val_stats['score']})
                    val_scores[algo_idx] = val_stats['score']
                next_eval += self.eval_every
                # If best total score, update best checkpoint.
                # Also save a best checkpoint on the first step.
                msg = (f'best avg val score was '
                       f'{best_score/len(self.algorithms):.3f}, '
                       f'current avg val score is {np.mean(val_scores):.3f}, '
                       f'val scores are: ')
                msg += ', '.join(
              ['%s: %.3f' % (x, y) for (x, y) in zip(self.algorithms, val_scores)])
                if (sum(val_scores) > best_score) or step == 0:
                    best_score = sum(val_scores)
                    #logging.info('Checkpointing best model, %s', msg)
                    print('Checkpointing best model, %s'% msg)
                    train_model.save_model('best.pkl')
                else:
                    #logging.info('Not saving new best model, %s', msg)
                    print('Not saving new best model, %s'% msg)
            
            step += 1
            length_idx = (length_idx + 1) % len(train_lengths)
            
        #logging.info('Restoring best model from checkpoint...')
        print('Restoring best model from checkpoint...')
        eval_model.restore_model('best.pkl', only_load_processor=False)
        
        for algo_idx in range(len(train_samplers)):
            common_extras = {'examples_seen': current_train_items[algo_idx],
                         'step': step,
                         'algorithm': self.algorithms[algo_idx]}
            new_rng_key, rng_key = jax.random.split(rng_key)
            test_stats = self.collect_and_eval(
                                test_samplers[algo_idx],
                                functools.partial(eval_model.predict, algorithm_index=algo_idx),
                                test_sample_counts[algo_idx],
                                new_rng_key,
                                extras=common_extras)
            #logging.info('(test) algo %s : %s', self.algorithms[algo_idx], test_stats)
            print('(test) algo %s : %s' % (self.algorithms[algo_idx], test_stats))
            self.record_test = test_stats
        
        #logging.info('Done!')
        print('Done!')
        self.model = eval_model
        
    def save_val_scores(self):
        """
        save to csv this model's score
        """
        df = pd.DataFrame.from_dict(self.record_val)
        df.to_csv(self.name + 'val_score.csv')
        #df = pd.DataFrame.from_dict(self.record_test)
        #df.to_csv(self.name + 'test_score.csv')

    


In [4]:
# List of GNN Architecture to use
processor_list = ['mpnn','deepsets', 'gat', 'gatv2', 'memnet_full' , 'pgn']

for processor in processor_list:
    GNN = functionalGNN(processor, 'hlflow_mincut', processor)
    GNN.train()
    GNN.save_val_scores()

Creating samplers for algo hlflow_mincut
num_samples  1000
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
computation done
comput

Generating splits...:   0%|          | 0/1 [00:00<?, ? splits/s]

Generating test examples...: 0 examples [00:00, ? examples/s]

Shuffling /tmp/CLRS30/dataset/CLRS30_v1.0.0/clrs_dataset/hlflow_mincut_test/1.0.0.incompleteXB8XM8/clrs_datase…

Dataset clrs_dataset downloaded and prepared to /tmp/CLRS30/dataset/CLRS30_v1.0.0/clrs_dataset/hlflow_mincut_test/1.0.0. Subsequent calls will reuse this data.
returning sampler for  test
Algo hlflow_mincut step 0 current loss 61.851746, current_train_items 32.
(val) algo hlflow_mincut step 0: {'S': 0.4343891402714933, 'score': 0.4343891402714933, 'examples_seen': 32, 'step': 0, 'algorithm': 'hlflow_mincut'}
Checkpointing best model, best avg val score was -1.000, current avg val score is 0.434, val scores are: hlflow_mincut: 0.434
Algo hlflow_mincut step 1 current loss 29.191666, current_train_items 64.
Algo hlflow_mincut step 2 current loss 25.225227, current_train_items 96.
Algo hlflow_mincut step 3 current loss 24.198513, current_train_items 128.
Algo hlflow_mincut step 4 current loss 22.797104, current_train_items 160.
Algo hlflow_mincut step 5 current loss 20.058529, current_train_items 192.
Algo hlflow_mincut step 6 current loss 17.894951, current_train_items 224.
Algo hlflow_mi